In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
%pip install spuco
%pip install -q pytorch-metric-learning
!pip install -q accelerate -U
!pip install -q transformers[torch]

In [3]:
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchvision.transforms as T
from torch.utils.data import DataLoader, Dataset
from spuco.datasets import SpuCoMNIST, SpuriousFeatureDifficulty
import torchvision.transforms as transforms
import cv2
import torchvision.models as models
from pytorch_metric_learning import losses
import torch.optim as optim
from torch.optim import lr_scheduler
import os

#device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
#Use CPU for analysis
device = "cpu"

In [4]:
magnitude = "LARGE"

magnitude_dict = {
    "SMALL": SpuriousFeatureDifficulty.MAGNITUDE_SMALL,
    "MEDIUM":SpuriousFeatureDifficulty.MAGNITUDE_MEDIUM,
    "LARGE":SpuriousFeatureDifficulty.MAGNITUDE_LARGE,
}

class Config:
  spurious_correlation_strength  = 0.995
  spurious_feature_difficulty = magnitude_dict[magnitude]
  label_noise = 0.001
  size = 28
  flip_probability = 0.5
  batch_size = 256
  backbone_pretrained = False
  projection_dim = 128
  T_max = 10
  lr = 5e-4
  min_lr = 1e-5
  weight_decay = 1e-6
  temperature = 0.5

In [5]:
model_type = 'ViTMAE'
save_dir = f"/content/drive/MyDrive/CS260D_final_project/plots/{model_type}/{Config.spurious_correlation_strength}_{magnitude}"
if not os.path.isdir(save_dir):
  os.makedirs(save_dir)

# Setup Data


In [6]:
classes = [[0, 1], [2, 3], [4, 5], [6, 7], [8, 9]]

trainset = SpuCoMNIST(
    root="/data/mnist/",
    spurious_feature_difficulty=Config.spurious_feature_difficulty,
    spurious_correlation_strength=Config.spurious_correlation_strength,
    classes=classes,
    split="train",
    label_noise=Config.label_noise
)

trainset.initialize()

valset = SpuCoMNIST(
    root="/data/mnist/",
    spurious_feature_difficulty=Config.spurious_feature_difficulty,
    spurious_correlation_strength=Config.spurious_correlation_strength,
    classes=classes,
    split="test",
    label_noise=Config.label_noise
)

valset.initialize()


100%|██████████| 10000/10000 [00:01<00:00, 5353.95it/s]


In [7]:
# Show example from each group
from IPython.display import display
for (k, v) in trainset.group_partition.items():
  print(f"Group: {k}, Qty: {len(v)}")
  img = T.ToPILImage()(trainset[v[0]][0])
  display(img)

Group: (2, 2), Qty: 8957


Group: (0, 0), Qty: 10074


Group: (4, 4), Qty: 9386


Group: (1, 1), Qty: 9609


Group: (3, 1), Qty: 17


...

Group: (2, 0), Qty: 18


Group: (4, 2), Qty: 12


Group: (4, 1), Qty: 13


Group: (3, 0), Qty: 7


Group: (4, 3), Qty: 18


In [7]:

## Augmentation
from torchvision.transforms import v2

size = 28
train_transform = transforms.Compose([
    v2.ToImage(),
    v2.RandomResizedCrop(size),
    v2.RandomHorizontalFlip(p=0.5),
    v2.RandomApply([transforms.ColorJitter(0.4, 0.4, 0.4, 0.1)], p=0.8),
    v2.RandomGrayscale(p=0.2),
    v2.ToTensor(),
    v2.Normalize([0.4914, 0.4822, 0.4465], [0.2023, 0.1994, 0.2010])])

test_transform = transforms.Compose([
    v2.ToImage(),
    v2.ToTensor(),
    v2.Normalize([0.4914, 0.4822, 0.4465], [0.2023, 0.1994, 0.2010])])

/usr/local/lib/python3.10/dist-packages/torchvision/transforms/v2/_deprecated.py:43: UserWarning: The transform `ToTensor()` is deprecated and will be removed in a future release. Instead, please use `v2.Compose([v2.ToImage(), v2.ToDtype(torch.float32, scale=True)])`.
  warnings.warn(


In [8]:
class SpucoDataset(Dataset):
    def __init__(self, dataset, transform=None):
        self.dataset = dataset
        self.transform = transform

    def __len__(self):
        return len(self.dataset)

    def __getitem__(self, index):
        img = self.dataset[index][0]
        label = self.dataset[index][1]

        if self.transform is None:
          self.transform = transforms.Compose([
          v2.ToImage(),
          v2.ToTensor(),
          v2.Normalize([0.4914, 0.4822, 0.4465], [0.2023, 0.1994, 0.2010])])

        augmented_img = self.transform(img)
        return augmented_img

In [9]:
train_dataset = SpucoDataset(trainset, train_transform)
val_dataset = SpucoDataset(valset, test_transform)

def collator_fn(batch):
  #return batch
  return { 'pixel_values': torch.stack(batch)
           }



# Setup Model

In [10]:
## https://github.com/berfukaraca/SSL-Cifar10-ContrastiveLearning/blob/main/colab_notebooks/SSL_SimCLR_Cifar10_CL.ipynb

from transformers import ViTMAEConfig, ViTMAEForPreTraining

modelConfig = ViTMAEConfig(
    hidden_size = 48,
    num_hidden_layers = 4,
    num_attention_heads = 4,
    intermediate_size = 256,
    hidden_act = 'gelu',
    hidden_dropout_prob = 0.0,
    attention_probs_dropout_prob = 0.0,
    initializer_range = 0.02,
    layer_norm_eps = 1e-12,
    image_size = 28,
    patch_size = 2,
    num_channels = 3,
    qkv_bias = True,
    decoder_num_attention_heads = 8,
    decoder_hidden_size = 64,
    decoder_num_hidden_layers = 6,
    decoder_intermediate_size = 224,
    mask_ratio = 0.75,
    norm_pix_loss = False
)



In [11]:

## model and optimizer
model = ViTMAEForPreTraining(modelConfig)
# print(model)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)

ViTMAEForPreTraining(
  (vit): ViTMAEModel(
    (embeddings): ViTMAEEmbeddings(
      (patch_embeddings): ViTMAEPatchEmbeddings(
        (projection): Conv2d(3, 48, kernel_size=(2, 2), stride=(2, 2))
      )
    )
    (encoder): ViTMAEEncoder(
      (layer): ModuleList(
        (0-3): 4 x ViTMAELayer(
          (attention): ViTMAEAttention(
            (attention): ViTMAESelfAttention(
              (query): Linear(in_features=48, out_features=48, bias=True)
              (key): Linear(in_features=48, out_features=48, bias=True)
              (value): Linear(in_features=48, out_features=48, bias=True)
              (dropout): Dropout(p=0.0, inplace=False)
            )
            (output): ViTMAESelfOutput(
              (dense): Linear(in_features=48, out_features=48, bias=True)
              (dropout): Dropout(p=0.0, inplace=False)
            )
          )
          (intermediate): ViTMAEIntermediate(
            (dense): Linear(in_features=48, out_features=256, bias=True)
        

In [12]:
from transformers import Trainer, TrainingArguments
args = TrainingArguments(
    output_dir = f"/content/drive/MyDrive/CS260D_final_project/model_parameters/ViTMAE/MNIST/{Config.spurious_correlation_strength}_{magnitude}/",
    evaluation_strategy = "epoch",
    label_names = ["pixel_values"],
    #eval_delay  = 2,
    logging_steps = 100,
    per_device_train_batch_size = Config.batch_size,
    per_device_eval_batch_size = Config.batch_size,
    learning_rate = 5e-4,
    num_train_epochs = 30,
    #lr_scheduler_type = "linear",
    save_strategy = "epoch",
    dataloader_num_workers = 2,
    load_best_model_at_end = True,
    fp16 = False,
    remove_unused_columns= False
)

In [13]:
class CustomTrainer(Trainer):

  def get_train_dataloader(self):
    collator = self.data_collator
    train_dataloader = DataLoader(dataset=train_dataset, batch_size=self.args.per_device_train_batch_size, num_workers=2, pin_memory=True, shuffle=True, collate_fn = collator)
    return train_dataloader

  def get_eval_dataloader(self, eval_dataset):
    collator = self.data_collator
    eval_dataset = eval_dataset if eval_dataset is not None else self.eval_dataset
    eval_dataloader = DataLoader(dataset=eval_dataset, batch_size=self.args.per_device_eval_batch_size, num_workers=2, pin_memory=True, shuffle=False, collate_fn = collator)
    return eval_dataloader

  def get_test_dataloader(self, test_dataset):
    collator = self.data_collator
    test_dataset = test_dataset if test_dataset is not None else self.test_dataset
    test_dataloader = DataLoader(dataset=test_dataset, batch_size=self.args.per_device_eval_batch_size, num_workers=2, pin_memory=True, shuffle=False, collate_fn = collator)
    return test_dataloader



trainer = CustomTrainer(
    model = model,
    args = args,
    data_collator = collator_fn,
    train_dataset = train_dataset,
    eval_dataset = val_dataset,
)

In [14]:
trainer.train(resume_from_checkpoint = True)

TrainOutput(global_step=5640, training_loss=0.0, metrics={'train_runtime': 0.2944, 'train_samples_per_second': 4891783.652, 'train_steps_per_second': 19157.889, 'total_flos': 8942027021706240.0, 'train_loss': 0.0, 'epoch': 30.0})

In [15]:
class SpucoDatasetwithLabels(Dataset):
    def __init__(self, dataset, transform=None):
        self.dataset = dataset
        self.transform = transform

    def __len__(self):
        return len(self.dataset)

    def __getitem__(self, index):
        img = self.dataset[index][0]
        label = self.dataset[index][1]

        if self.transform is None:
          self.transform = transforms.Compose([
          v2.ToImage(),
          v2.ToTensor(),
          v2.Normalize([0.4914, 0.4822, 0.4465], [0.2023, 0.1994, 0.2010])])

        augmented_img = self.transform(img)
        return augmented_img, label

In [16]:

import matplotlib.pyplot as plt
import numpy as np
from sklearn.decomposition import PCA
from tqdm import tqdm

val_dataset_labels = SpucoDatasetwithLabels(valset)
val_dataloader = DataLoader(dataset=val_dataset_labels, batch_size=Config.batch_size, num_workers=2, pin_memory=True, shuffle=False)

In [17]:
## Generate tensor of all embeddings and targets on CPU

import matplotlib.pyplot as plt
import pandas as pd
from sklearn.decomposition import PCA

torch.cuda.empty_cache()
device = 'cpu'
model.to(device)


embeddings = []
targets = []

for batch_idx, (images, labels) in enumerate(val_dataloader):
  encoded_output = model.vit(images)
  #decoded_output = model.decoder(**encoded_output)
  embeddings.append(encoded_output['last_hidden_state'][:, 0, :].flatten(1, -1).detach().cpu())
  targets.append(labels)

embeddings = torch.cat(embeddings).detach().cpu().numpy()
targets = torch.cat(targets).cpu().numpy()

/usr/local/lib/python3.10/dist-packages/torchvision/transforms/v2/_deprecated.py:43: UserWarning: The transform `ToTensor()` is deprecated and will be removed in a future release. Instead, please use `v2.Compose([v2.ToImage(), v2.ToDtype(torch.float32, scale=True)])`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torchvision/transforms/v2/_deprecated.py:43: UserWarning: The transform `ToTensor()` is deprecated and will be removed in a future release. Instead, please use `v2.Compose([v2.ToImage(), v2.ToDtype(torch.float32, scale=True)])`.
  warnings.warn(


# Data Analysis

In [18]:
comp = 32
pca = PCA(n_components=comp)
pca_emb = pca.fit_transform(embeddings)
PCs = pd.DataFrame(pca_emb)
PCs.columns = [f"PC{i+ 1}" for i in range(comp)]
embs = pd.concat([pd.DataFrame(embeddings),PCs], axis=1, join='inner')

In [19]:
# Check singular values for pca
pca.singular_values_

array([297.90262   , 106.37784   ,  85.59776   ,  49.889977  ,
        18.734135  ,  14.124857  ,   8.24218   ,   3.7406104 ,
         3.0907564 ,   2.6807315 ,   2.407161  ,   2.0196626 ,
         1.76826   ,   1.5501205 ,   1.2766216 ,   1.220927  ,
         1.0787985 ,   1.0109309 ,   0.97386795,   0.9071018 ,
         0.775154  ,   0.7541219 ,   0.73168844,   0.66150427,
         0.6288046 ,   0.5457391 ,   0.5168483 ,   0.4835123 ,
         0.45929134,   0.4308464 ,   0.4055224 ,   0.39342397],
      dtype=float32)

In [20]:
# Add labels to embedding df
embs['true_label'] = targets
for (true, spur), idxs in valset.group_partition.items():
  for i in idxs:
    embs.loc[i, 'spurious_label'] = spur
embs['spurious_label'] = embs['spurious_label'].astype(int)

## Full Data Analysis

### PCA

In [ ]:
import plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

traces = []
for (true_label, spurious_label), df in embs.groupby(['true_label', 'spurious_label']):
  traces.append(go.Scatter(x = df['PC1'],
                           y = df['PC2'],
                           mode = "markers",
                           name = f"True label {true_label}, Spurious label {spurious_label}",
                           text = None,
                           marker = dict(size = 4)
                           )
  )
title = "PCA analysis of Validation Data by Group"
layout = dict(title = title,
              xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
              yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
              height = 1000,
              width = 1000
             )

fig = dict(data = traces, layout = layout)
iplot(fig)
save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_alldata_by_groups.html"
go.Figure.write_html(fig, os.path.join(save_dir, save_name))

In [22]:
import plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

traces = []
for true_label, df in embs.groupby(['true_label']):
  traces.append(go.Scatter(x = df['PC1'],
                           y = df['PC2'],
                           mode = "markers",
                           name = f"True label {true_label}",
                           text = None,
                           marker = dict(size = 4)
                           )
  )
title = "PCA analysis of Validation Data by True Label"
layout = dict(title = title,
              xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
              yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
              height = 1000,
              width = 1000
             )

fig = dict(data = traces, layout = layout)
iplot(fig)
save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_alldata_by_truelabel.html"
go.Figure.write_html(fig, os.path.join(save_dir, save_name))

<ipython-input-22-4a5026f7690c>:6: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



In [23]:
import plotly as py
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

traces = []
for spurious_label, df in embs.groupby(['spurious_label']):
  traces.append(go.Scatter(x = df['PC1'],
                           y = df['PC2'],
                           mode = "markers",
                           name = f"Spurious label {spurious_label}",
                           text = None,
                           marker = dict(size = 4)
                           )
  )
title = "PCA analysis of Validation Data by Spurious Label"
layout = dict(title = title,
              xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
              yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
              height = 1000,
              width = 1000
             )

fig = dict(data = traces, layout = layout)
iplot(fig)
save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_alldata_by_spuriouslabel.html"
go.Figure.write_html(fig, os.path.join(save_dir, save_name))

<ipython-input-23-409e73fd8e41>:6: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



### t-SNE

In [ ]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:

#T-SNE with two dimensions
  tsne = TSNE(n_components=2, perplexity=perplexity, n_iter = 3000)

  TCs = pd.DataFrame(tsne.fit_transform(embeddings))
  TCs.columns = ["TC1","TC2"]
  TCs['true_label'] = embs['true_label']
  TCs['spurious_label'] = embs['spurious_label']
  # Find best perplexity value
  traces = []
  for (true_label, spurious_label), df in TCs.groupby(['true_label', 'spurious_label']):
    traces.append(go.Scatter(x = df['TC1'], y = df['TC2'], mode = "markers", name = f"True label {true_label}, Spurious label {spurious_label}", text = None))

  title = f"t-SNE Cluster Visualization of Embedded Data, Perplexity = {perplexity}"
  layout = dict(title = title,
                xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
                #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
              )

  fig = dict(
      data = traces,
      layout = layout
  )
  iplot(fig)

  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_alldata_by_groups.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))


# tsne_embs = pd.concat([embs,TCs], axis=1, join='inner')

In [24]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:

#T-SNE with two dimensions
  tsne = TSNE(n_components=2, perplexity=perplexity, n_iter = 3000)

  TCs = pd.DataFrame(tsne.fit_transform(embeddings))
  TCs.columns = ["TC1","TC2"]
  TCs['true_label'] = embs['true_label']
  TCs['spurious_label'] = embs['spurious_label']
  # Find best perplexity value
  traces = []
  for true_label, df in TCs.groupby(['true_label']):
    traces.append(go.Scatter(x = df['TC1'], y = df['TC2'], mode = "markers", name = f"True label {true_label}", text = None))

  title = f"t-SNE Cluster Visualization of Embedded Data Grouped by True Label, Perplexity = {perplexity}"
  layout = dict(title = title,
                xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
                #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
              )

  fig = dict(
      data = traces,
      layout = layout
  )
  iplot(fig)

  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_alldata_by_truelabel.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))


# tsne_embs = pd.concat([embs,TCs], axis=1, join='inner')

<ipython-input-24-173cbd2d105d>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



<ipython-input-24-173cbd2d105d>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



<ipython-input-24-173cbd2d105d>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



In [25]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:

#T-SNE with two dimensions
  tsne = TSNE(n_components=2, perplexity=perplexity, n_iter = 3000)

  TCs = pd.DataFrame(tsne.fit_transform(embeddings))
  TCs.columns = ["TC1","TC2"]
  TCs['true_label'] = embs['true_label']
  TCs['spurious_label'] = embs['spurious_label']
  # Find best perplexity value
  traces = []
  for spurious_label, df in TCs.groupby(['spurious_label']):
    traces.append(go.Scatter(x = df['TC1'], y = df['TC2'], mode = "markers", name = f"Spurious label {spurious_label}", text = None))

  title = f"t-SNE Cluster Visualization of Embedded Data Grouped by Spurious Label, Perplexity = {perplexity}"
  layout = dict(title = title,
                xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
                #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
              )

  fig = dict(
      data = traces,
      layout = layout
  )
  iplot(fig)

  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_alldata_by_spuriouslabel.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))


# tsne_embs = pd.concat([embs,TCs], axis=1, join='inner')

<ipython-input-25-3e5136d599d5>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



<ipython-input-25-3e5136d599d5>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



<ipython-input-25-3e5136d599d5>:14: FutureWarning:

In a future version of pandas, a length 1 tuple will be returned when iterating over a groupby with a grouper equal to a list of length 1. Don't supply a list with a single grouper to avoid this warning.



### PCA --> t-SNE

In [ ]:
from sklearn.manifold import TSNE

for perplexity in [30, 50, 100]:

#T-SNE with two dimensions
  tsne = TSNE(n_components=2, perplexity=perplexity, n_iter = 3000)

  TCs = pd.DataFrame(tsne.fit_transform(pca_emb))
  TCs.columns = ["TC1","TC2"]
  TCs['true_label'] = embs['true_label']
  TCs['spurious_label'] = embs['spurious_label']
  # Find best perplexity value
  traces = []
  for (true_label, spurious_label), df in TCs.groupby(['true_label', 'spurious_label']):
    traces.append(go.Scatter(x = df['TC1'], y = df['TC2'], mode = "markers", name = f"True label {true_label}, Spurious label {spurious_label}", text = None))

  title = f"t-SNE Cluster Visualization of PCA Embedded Data, Perplexity = {perplexity}"
  layout = dict(title = title,
                xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
                #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
              )

  fig = dict(
      data = traces
  )
  iplot(fig)


  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCAtoTSNE_perplexity{perplexity}_alldata_by_groups.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))

# tsne_embs = pd.concat([embs,TCs], axis=1, join='inner')

## Analysis in Each True Label

### PCA

In [26]:
true_label_clusters_pca = {
    # True label: embedding dataframe
}
for l, true_cluster in embs.groupby('true_label'):
  true_emb = true_cluster.iloc[:, :128].values
  comp = 15
  pca = PCA(n_components=comp)

  PCs = pd.DataFrame(pca.fit_transform(true_emb), columns = [f"PC{i+ 1}_TL" for i in range(comp)])
  PCs = pd.concat([PCs,true_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
  true_label_clusters_pca[l] = PCs
  print(pca.singular_values_)
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


[94.70773836 65.03709913 18.37762056  8.52114001  7.43558253  4.93183861
  3.21565424  2.79046285  2.02871786  2.01000843  1.58427673  1.40125318
  1.26461991  1.22315117  1.1258902 ]
[63.92296745 52.46219366  8.30143594  5.36539064  4.81359326  3.29537418
  2.46119255  1.91967241  1.73091025  1.51740238  1.35552282  1.08730676
  0.98556966  0.83702558  0.78534438]
[61.63348964 55.4476996   8.43000312  5.70250463  5.20095406  3.84459472
  2.4781389   1.90709436  1.85541164  1.46143789  1.39054684  1.07756007
  1.02177785  0.87765406  0.82123682]
[63.60322127 61.03153696 10.81266206  6.08810444  5.41696585  3.90305991
  2.57584807  2.01011727  1.89740471  1.7188807   1.42525254  1.16440026
  1.0923045   0.99895889  0.90319811]
[62.98434467 51.86236858  7.69701449  5.3935459   4.98277438  3.51525038
  2.41744846  1.84529486  1.74740007  1.48755949  1.40168145  1.06191217
  0.9938168   0.86415443  0.76084928]


In [27]:
import os

for k, v in true_label_clusters_pca.items():
  traces = []
  for s in np.sort(v['spurious_label'].unique()):
    group = v[v['spurious_label'] == s]
    traces.append(go.Scatter(
                      x = group['PC1_TL'],
                      y = group['PC2_TL'],
                      #z = group['PC3_TL'],
                      mode = "markers",
                      name = f"Subgroup {s}",
                      text = None))
  data = traces

  title = f"True Label {k} PCA"

  layout = dict(title = title,
                xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
              )

  fig = dict(data = data, layout = layout)


  iplot(fig)
  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_on_TL{k}.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))

### t-SNE

In [28]:
true_label_clusters_tsne = {
    # True label: embedding dataframe
}
for l, true_cluster in embs.groupby('true_label'):
  true_emb = true_cluster.iloc[:, :128].values
  comp = 2
  tsne = TSNE(n_components=comp)

  TCs = pd.DataFrame(tsne.fit_transform(true_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
  TCs = pd.concat([TCs,true_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
  true_label_clusters_tsne[l] = TCs
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


In [21]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:
  true_label_clusters_tsne = {
    # True label: embedding dataframe
  }
  for l, true_cluster in embs.groupby('true_label'):
    true_emb = true_cluster.iloc[:, :128].values
    comp = 2
    tsne = TSNE(n_components=comp, perplexity = perplexity, n_iter = 3000)

    TCs = pd.DataFrame(tsne.fit_transform(true_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
    TCs = pd.concat([TCs,true_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
    true_label_clusters_tsne[l] = TCs

  for k, v in true_label_clusters_tsne.items():
    traces = []
    for s in np.sort(v['spurious_label'].unique()):
      group = v[v['spurious_label'] == s]
      traces.append(go.Scatter(
                        x = group['TC1_TL'],
                        y = group['TC2_TL'],
                        #z = group['TC3_TL'],
                        mode = "markers",
                        name = f"Spurious Label {s}",
                        text = None,
                        marker = dict(size = 4)
                        ))
    data = traces

    title = f"t-SNE Analysis of Spurious Label {k} Embeddings, Perplexity {perplexity}"

    layout = dict(title = title,
                  xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                  yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                  #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
                  width = 1000,
                  height = 1000
                )

    fig = dict(data = data, layout = layout)
    iplot(fig)
    save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_on_TL{k}.html"
    go.Figure.write_html(fig, os.path.join(save_dir, save_name))
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


NameError: ignored

### PCA --> t-SNE

In [30]:
from sklearn.manifold import TSNE

for perplexity in [15, 30, 50]:
  true_label_clusters_pca_tsne = {
    # True label: embedding dataframe
  }
  for l, true_cluster_pca_df in true_label_clusters_pca.items():
    true_emb = true_cluster_pca_df.iloc[:, :-2].values
    comp = 2
    tsne = TSNE(n_components=comp, perplexity = perplexity, n_iter = 3000)

    TCs = pd.DataFrame(tsne.fit_transform(true_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
    TCs = pd.concat([TCs,true_cluster_pca_df[['true_label', 'spurious_label']]], axis=1, join='inner')
    true_label_clusters_pca_tsne[l] = TCs

  for k, v in true_label_clusters_pca_tsne.items():
    traces = []
    for s in np.sort(v['spurious_label'].unique()):
      group = v[v['spurious_label'] == s]
      traces.append(go.Scatter(
                        x = group['TC1_TL'],
                        y = group['TC2_TL'],
                        #z = group['TC3_TL'],
                        mode = "markers",
                        name = f"Spurious Label {s}",
                        text = None,
                        marker = dict(size = 4)
                        ))
    data = traces

    title = f"t-SNE Analysis of True Label {k} PCA Embeddings, Perplexity {perplexity}"

    layout = dict(title = title,
                  xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                  yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                  #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
                  width = 1000,
                  height = 1000
                )

    fig = dict(data = data, layout = layout)
    iplot(fig)
    save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCAtoTSNE_perplexity{perplexity}_on_TL{k}.html"
    go.Figure.write_html(fig, os.path.join(save_dir, save_name))
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


## Analysis in Each Spurious Label

### PCA

In [ ]:
spurious_label_clusters_pca = {
    # True label: embedding dataframe
}
for l, spurious_cluster in embs.groupby('spurious_label'):
  spur_emb = spurious_cluster.iloc[:, :128].values
  comp = 15
  pca = PCA(n_components=comp)

  PCs = pd.DataFrame(pca.fit_transform(spur_emb), columns = [f"PC{i+ 1}_TL" for i in range(comp)])
  PCs = pd.concat([PCs,spurious_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
  spurious_label_clusters_pca[l] = PCs
  print(pca.singular_values_)
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


In [ ]:
for k, v in spurious_label_clusters_pca.items():
  traces = []
  for s in np.sort(v['true_label'].unique()):
    group = v[v['true_label'] == s]
    traces.append(go.Scatter(
                      x = group['PC1_TL'],
                      y = group['PC2_TL'],
                      #z = group['PC3_TL'],
                      mode = "markers",
                      name = f"Subgroup {s}",
                      text = None))
  data = traces

  title = f"Spurious Label {k} PCA"

  layout = dict(title = title,
                xaxis= dict(title= 'PC1',ticklen= 5,zeroline= False),
                yaxis= dict(title= 'PC2',ticklen= 5,zeroline= False),
                width = 1000,
                height = 1000
              )

  fig = dict(data = data, layout = layout)


  iplot(fig)
  save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCA_on_SL{k}.html"
  go.Figure.write_html(fig, os.path.join(save_dir, save_name))

### t-SNE

In [31]:
spurious_label_clusters_tsne = {
    # True label: embedding dataframe
}
for l, spurious_cluster in embs.groupby('spurious_label'):
  spur_emb = spurious_cluster.iloc[:, :128].values
  comp = 2
  tsne = TSNE(n_components=comp)

  TCs = pd.DataFrame(tsne.fit_transform(spur_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
  TCs = pd.concat([TCs,spurious_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
  spurious_label_clusters_tsne[l] = TCs
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


In [ ]:
for perplexity in [15, 30, 50]:
  spurious_label_clusters_tsne = {
    # True label: embedding dataframe
  }
  for l, spurious_cluster in embs.groupby('spurious_label'):
    spur_emb = spurious_cluster.iloc[:, :128].values
    comp = 2
    tsne = TSNE(n_components=comp, perplexity = perplexity, n_iter = 3000)

    TCs = pd.DataFrame(tsne.fit_transform(spur_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
    TCs = pd.concat([TCs,spurious_cluster[['true_label', 'spurious_label']]], axis=1, join='inner')
    spurious_label_clusters_tsne[l] = TCs

  for k, v in spurious_label_clusters_tsne.items():
    traces = []
    for s in np.sort(v['true_label'].unique()):
      group = v[v['true_label'] == s]
      traces.append(go.Scatter(
                        x = group['TC1_TL'],
                        y = group['TC2_TL'],
                        #z = group['TC3_TL'],
                        mode = "markers",
                        name = f"True Label {s}",
                        text = None,
                        marker = dict(size = 4)
                        ))
    data = traces

    title = f"t-SNE Analysis of Spurious Label {k} Embeddings, Perplexity {perplexity}"

    layout = dict(title = title,
                  xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                  yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                  #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
                  width = 1000,
                  height = 1000
                )

    fig = dict(data = data, layout = layout)
    iplot(fig)
    save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_TSNE_perplexity{perplexity}_on_SL{k}.html"
    go.Figure.write_html(fig, os.path.join(save_dir, save_name))
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')


### PCA --> t-SNE

In [ ]:
for perplexity in [15, 30, 50]:
  spurious_label_clusters_pca_tsne = {
    # True label: embedding dataframe
  }
  for l, spurious_cluster_pca_df in spurious_label_clusters_pca.items():
    spurious_emb = spurious_cluster_pca_df.iloc[:, :-2].values
    comp = 2
    tsne = TSNE(n_components=comp, perplexity = perplexity, n_iter = 3000)

    TCs = pd.DataFrame(tsne.fit_transform(spurious_emb), columns = [f"TC{i+ 1}_TL" for i in range(comp)])
    TCs = pd.concat([TCs,spurious_cluster_pca_df[['true_label', 'spurious_label']]], axis=1, join='inner')
    spurious_label_clusters_pca_tsne[l] = TCs

  for k, v in spurious_label_clusters_pca_tsne.items():
    traces = []
    for s in np.sort(v['true_label'].unique()):
      group = v[v['true_label'] == s]
      traces.append(go.Scatter(
                        x = group['TC1_TL'],
                        y = group['TC2_TL'],
                        #z = group['TC3_TL'],
                        mode = "markers",
                        name = f"True Label {s}",
                        text = None,
                        marker = dict(size = 4)
                        ))
    data = traces

    title = f"T-SNE Analysis of Spurious Label {k} PCA Embeddings, Perplexity {perplexity}"

    layout = dict(title = title,
                  xaxis= dict(title= 'TC1',ticklen= 5,zeroline= False),
                  yaxis= dict(title= 'TC2',ticklen= 5,zeroline= False),
                  #zaxis= dict(title= 'TC3',ticklen= 5,zeroline= False)
                  width = 1000,
                  height = 1000
                )

    fig = dict(data = data, layout = layout)
    iplot(fig)
    save_name = f"{model_type}_{Config.spurious_correlation_strength}_{magnitude}_PCAtoTSNE_perplexity{perplexity}_on_SL{k}.html"
    go.Figure.write_html(fig, os.path.join(save_dir, save_name))
  # pca_embs = pd.concat([pd.DataFrame(embeddings),PCs_2d], axis=1, join='inner')
